# Traffic analysis - Madrid Central

In this notebook we want to analyze if there is a significant change in the use of traffic inside the area of Madrid Central when the measure was instaured. For that we analyze data from 2016 until 2021.

## Imports

In [34]:
import pandas as pd
import numpy as np
import requests
import matplotlib.pyplot as plt
from matplotlib.path import Path
import json
import zipfile
import io
import os
import utm
import seaborn as sns

from IPython.display import display

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import HoverTool, Legend, ColumnDataSource,\
                        Title, GeoJSONDataSource, DatetimeTickFormatter,\
                        Span, CheckboxGroup, CustomJS, Button
from bokeh.tile_providers import get_provider, CARTODBPOSITRON
from bokeh.transform import linear_cmap, dodge
from bokeh.layouts import row, column

from tqdm import tqdm

output_notebook()
np.random.seed(42)

Loading BokehJS ...

## Data download

The data we want to work with is very large, thus we need to download it from the source as it is not possible to upload it to the version control system we use (GitHub). 

In [2]:
def download_data():
    """ Download all traffic data from January 2016 (ID=32) until December 2021 (ID=103)
        Some files do not follow the same naming convention, and need repairing.
        The name convention that most files follow is '{num_month}-{num_year}.yaml',
        so everyone will follow that
    """
    FIRST_MONTH_ID = 32
    LAST_MONTH_ID = 103
    DATA_PATH = "data"
    
    for month_id in tqdm(range(FIRST_MONTH_ID, LAST_MONTH_ID+1), desc="Downloading data", unit="file"):
        
        # Get month number, from 1 to 12
        current_month = ((month_id - FIRST_MONTH_ID) % 12) + 1
        
        # Get year number, from 2016 to 2021
        current_year = int((month_id - FIRST_MONTH_ID) / 12) + 2016    
               
        # If it has been downloaded already, skip it

        file_path = f"{DATA_PATH}/{current_month:02d}-{current_year}.csv"

        if not os.path.isfile(file_path):

            url = f"https://datos.madrid.es/egob/catalogo/208627-{month_id}-transporte-ptomedida-historico.zip"
            r = requests.get(url)
            z = zipfile.ZipFile(io.BytesIO(r.content))
            zipcsv = z.infolist()[-1]
            
            # Rename file
            zipcsv.filename = file_path
            
            # Extract file
            z.extract(zipcsv)

In [3]:
do_download = int(input("WRITE '1' TO DOWNLOAD DATA OR '0' TO NOT "))

if do_download:
    download_data()

## Display location of traffic measurement points

Before diving into the actual data, we need to contextualize. Madrid is divided into districts. There are *21* one of them, being the area of **Madrid Central** exactly the same as the **Centro district** area (thus the name).

We have a dataset of where the measure of traffic points are located. As expected, they are not evenly distributed. Our first task is to see in which district each traffic measurement point is located.

In [4]:
traffic_points = pd.read_csv("shared_data/traffic_points/pmed_trafico_03052016.csv", sep=";")
traffic_points.head()

idelem  tipo_elem    cod_cent                                    nombre  \
0    1044        494  03FT08PM01                                03FT08PM01   
1    3600        494     PM30901                                   PM30901   
2    3705        494     PM41451                                   PM41451   
3    6823        494     PM41453                                   PM41453   
4    7033        495       01015  Pº Castellana S-N - Pl. Colon-Hermosilla   

            st_x          st_y  
0  438963.314635  4.474734e+06  
1  443729.047369  4.473268e+06  
2  439858.261097  4.471574e+06  
3  439188.095183  4.470895e+06  
4  441569.555897  4.475502e+06

First we need to calculate the correct *utm* for displaying in `bokeh` maps.

In [5]:
def utm_from_latlon(lat, lon):
    """ From a given lat and lon, calculates the correct UTM coordinates to 
        plot using `bokeh` 
    """
    r_major = 6378137.000
    x = r_major * np.radians(lon)
    scale = x/lon
    y = 180.0/np.pi * np.log(np.tan(np.pi/4.0 + 
        lat * (np.pi/180.0)/2.0)) * scale

    return x, y

def get_lat_lon_utm(row):
    """ From a row containing the columns 'st_x' and 'st_y' calculates both the lat and lon
        and the correct UTM coordinates to plot using `bokeh`
    """

    # 30 and 'T' is the zone of Madrid
    lat, lon = utm.to_latlon(row["st_x"], row["st_y"], 30, "T")
    
    x, y = utm_from_latlon(lat, lon)

    return pd.Series([lat, lon, x, y])

In [6]:
traffic_points[["latitude", "longitude", "utm_x", "utm_y"]] = traffic_points.apply(get_lat_lon_utm, axis=1)
traffic_points.head()

idelem  tipo_elem    cod_cent                                    nombre  \
0    1044        494  03FT08PM01                                03FT08PM01   
1    3600        494     PM30901                                   PM30901   
2    3705        494     PM41451                                   PM41451   
3    6823        494     PM41453                                   PM41453   
4    7033        495       01015  Pº Castellana S-N - Pl. Colon-Hermosilla   

            st_x          st_y   latitude  longitude          utm_x  \
0  438963.314635  4.474734e+06  40.421001  -3.719488 -414051.481782   
1  443729.047369  4.473268e+06  40.408129  -3.663184 -407783.811885   
2  439858.261097  4.471574e+06  40.392598  -3.708640 -412843.963659   
3  439188.095183  4.470895e+06  40.386431  -3.716471 -413715.710072   
4  441569.555897  4.475502e+06  40.428107  -3.688839 -410639.639249   

          utm_y  
0  4.927311e+06  
1  4.925429e+06  
2  4.923159e+06  
3  4.922257e+06  
4  4.928350e+06

Then load the districts information to display them in the map.

In [7]:
with open("shared_data/districts/districts.geojson", "r") as geojson:
    geodata = json.load(geojson)

In [8]:
df_districts = pd.DataFrame([], columns=["name", "latitude",
                                         "longitude", "utm_x",
                                         "utm_y"])
for district in geodata["features"]:
    # Get district name
    district_name = district["properties"]["NOMBRE"]
    
    # Get district coordinates
    district_coord = district["geometry"]["coordinates"][0]
    df_district = pd.DataFrame(district["geometry"]["coordinates"][0], columns=["st_x", "st_y"])
    df_district["name"] = district_name
    
    # Calculate correct utm
    df_district[["latitude", "longitude", "utm_x", "utm_y"]] = df_district.apply(get_lat_lon_utm, axis=1)
    df_district = df_district.drop(columns=["st_x", "st_y"])
    
    # Append to all districts dataframe
    df_districts = pd.concat([df_districts, df_district]).reset_index(drop=True)


district_name = df_districts["name"].unique()
df_districts

name   latitude  longitude          utm_x         utm_y
0                Centro  40.407345  -3.693162 -411120.867401  4.925314e+06
1                Centro  40.407196  -3.693202 -411125.341089  4.925293e+06
2                Centro  40.406986  -3.693227 -411128.197118  4.925262e+06
3                Centro  40.407127  -3.693677 -411178.251532  4.925282e+06
4                Centro  40.407256  -3.693849 -411197.420454  4.925301e+06
...                 ...        ...        ...            ...           ...
9466  Moncloa - Aravaca  40.469899  -3.802628 -423306.659924  4.934464e+06
9467  Moncloa - Aravaca  40.469823  -3.802359 -423276.645066  4.934452e+06
9468  Moncloa - Aravaca  40.469748  -3.802093 -423247.039940  4.934441e+06
9469  Moncloa - Aravaca  40.469672  -3.801822 -423216.881019  4.934430e+06
9470  Moncloa - Aravaca  40.469448  -3.801040 -423129.799177  4.934398e+06

[9471 rows x 5 columns]

Save in which district is each traffic point

In [9]:
traffic_points["district"] = "None"
points = traffic_points[["utm_x", "utm_y"]]

for name in district_name:
    path = Path(df_districts[df_districts["name"] == name][["utm_x", "utm_y"]])
    points_in_path_mask = path.contains_points(points)
    traffic_points.loc[points_in_path_mask, "district"] = name

# Discard the traffic points outside any district of Madrid, as they are outside the city
    
traffic_points = traffic_points.drop(traffic_points[traffic_points["district"] == "None"].index)\
                .reset_index(drop=True)

traffic_points.head()

idelem  tipo_elem    cod_cent                                    nombre  \
0    1044        494  03FT08PM01                                03FT08PM01   
1    3600        494     PM30901                                   PM30901   
2    3705        494     PM41451                                   PM41451   
3    6823        494     PM41453                                   PM41453   
4    7033        495       01015  Pº Castellana S-N - Pl. Colon-Hermosilla   

            st_x          st_y   latitude  longitude          utm_x  \
0  438963.314635  4.474734e+06  40.421001  -3.719488 -414051.481782   
1  443729.047369  4.473268e+06  40.408129  -3.663184 -407783.811885   
2  439858.261097  4.471574e+06  40.392598  -3.708640 -412843.963659   
3  439188.095183  4.470895e+06  40.386431  -3.716471 -413715.710072   
4  441569.555897  4.475502e+06  40.428107  -3.688839 -410639.639249   

          utm_y           district  
0  4.927311e+06  Moncloa - Aravaca  
1  4.925429e+06          Moratalaz  
2  4.923159e+06        Carabanchel  
3  4.922257e+06        Carabanchel  
4  4.928350e+06          Salamanca

In [10]:
district_colors = sns.color_palette('Spectral', len(district_name))
np.random.shuffle(district_colors)
district_colors

[(0.7126489811610919, 0.10711264898116109, 0.28081507112648985),
 (0.3600153787004998, 0.7161860822760476, 0.6655132641291811),
 (0.5910034602076126, 0.835524798154556, 0.6442906574394464),
 (0.8141484044598232, 0.2196847366397539, 0.3048058439061899),
 (0.9963860053825452, 0.8879661668589004, 0.5610918877354863),
 (0.9817762399077278, 0.6073817762399076, 0.3457900807381776),
 (0.9557862360630527, 0.9823144944252211, 0.6800461361014996),
 (0.9330257593233372, 0.3913110342176086, 0.27197231833910035),
 (0.26405228758169935, 0.6091503267973857, 0.7098039215686275),
 (0.47427912341407163, 0.7898500576701268, 0.6459823144944252),
 (0.8202998846597465, 0.9275663206459055, 0.6126874279123413),
 (0.8758169934640523, 0.3045751633986928, 0.29411764705882354),
 (0.9982314494425221, 0.9451749327181853, 0.6570549788542868),
 (0.2941945405613224, 0.4062283737024224, 0.680968858131488),
 (0.9665513264129182, 0.49742406766628217, 0.295040369088812),
 (0.9096501345636295, 0.9638600538254518, 0.6080738177623992),
 (0.9946943483275663, 0.8092272202998846, 0.48696655132641287),
 (0.998077662437524, 0.9992310649750096, 0.7460207612456747),
 (0.7114186851211075, 0.8832756632064592, 0.6348327566320646),
 (0.21299500192233756, 0.5114186851211072, 0.730795847750865),
 (0.9928489042675894, 0.716955017301038, 0.40945790080738165)]

In [11]:
def get_color_from_palette(color):
    """ Getting colors for plotting """
    return tuple([int(c * 255) for c in color])

def get_dark_color_from_palette(color):
    """ Getting darker colors for plotting """
    return tuple([int(c * 200) for c in color])

In [12]:
p = figure(title="Traffic measurement points", x_axis_type="mercator", y_axis_type="mercator",
           height=700, width=800)


for name, color in zip(district_name, district_colors):
    # Districts
    source = ColumnDataSource(df_districts[df_districts["name"] == name])
    p.patch(x="utm_x", y="utm_y", color=get_color_from_palette(color), line_width=3, alpha=0.4, 
            source=source, legend_label=name, muted=True, muted_alpha=0.1)
    # Traffic points
    source = ColumnDataSource(traffic_points[traffic_points["district"] == name])
    p.circle(x="utm_x", y="utm_y", color=get_color_from_palette(color), line_width=1,
            source=source, legend_label=name, muted=True, muted_alpha=0.3, radius=30,
            line_color=get_dark_color_from_palette(color))
    
# Madrid Central
source = ColumnDataSource(df_districts[df_districts["name"] == "Centro"])
p.line(x="utm_x", y="utm_y", color="black", line_width=2, 
        source=source, legend_label="Madrid Central limit", muted=False, muted_alpha=0.3)

        

# Hover tooltip
TOOLTIPS = [
    ("Name", "@nombre"),
    ("District", "@district")
]
p.add_tools(HoverTool(tooltips=TOOLTIPS))

cartodb = get_provider(CARTODBPOSITRON)
p.add_tile(cartodb)
p.add_layout(p.legend[0], "right")
p.legend.click_policy = "mute"
show(p)

## Loading traffic information

The next step is to finally load the datasets for traffic information. This datasets have a lot of rows, as each of the more than 3000 measurement points record mutiple parameters each 15 minutes, so a rough approximation of how many rows each month file has is:

$$ 30(days) \cdot 24(hours) \cdot 4(measures\_per\_hour) \cdot 3000(traffic\_points) = 8640000 $$

And once again, if we take into account that we are using data from 2016 until the end of 2021, a more accurate row count would be:

$$ 6(years) \cdot 365(days) \cdot 24(hours) \cdot 4(measures\_per\_hour) \cdot 3000(traffic\_points) = 630720000 $$

This amount of data (more than 630 million rows) is too much to handle efficiently, and obtain relevant information (REWRITE THIS A BIT, SEEMS MORE TO BE AN EXCUSE RATHER THAN A DECISION). To reduce the amount of rows, we decide on keeping the average intensity of traffic (Number of cars) per day in each district. That way, we will have:

$$ 6(years) \cdot 365(days) \cdot 21(number\_districts) = 45990 $$

which is more manageable number, from where we aspire to detect the relevant information in the data. Around 13714 times less data.

In [13]:
def process_traffic_data(filepath, traffic_points_df):
    """ Function to process each traffic data file. This preoprocess has as objective to reduce
        the dimensionality od the data, only keeping one value per district per day, reducing this
        way the number of rows to handle.
        
        Arguments:
            filepath          -> path to load the csv
            traffic_points_df -> traffic_points dataset (where they are located)
    """
    
    # Load file
    traffic_df = pd.read_csv(filepath, sep=";")
    
    # For god knows why, there is one file that is separated by ',' instead of ';'
    # so we reread the file if it only has one column
    if len(traffic_df.columns) == 1:
        traffic_df = pd.read_csv(filepath, sep=",")
    
    # If the 'idelem' column does not exists, is because is called 'id', so rename column
    if "idelem" not in traffic_df.columns:
        traffic_df = traffic_df.rename(columns = {'id':'idelem'})
    
    # Use only the traffic points for whom we have information 
    traffic_df = traffic_df[traffic_df["idelem"].isin(traffic_points_df["idelem"])]
    
    # Transform date to datime type
    traffic_df["fecha"] = pd.to_datetime(traffic_df["fecha"])
    
    # Get date in separate columns
    traffic_df["day"] = traffic_df["fecha"].dt.day
    traffic_df["month"] = traffic_df["fecha"].dt.month
    traffic_df["year"] = traffic_df["fecha"].dt.year

    # Group by id and date, up to day, and get the average intensity perr traffic point
    traffic_df = traffic_df.groupby(["idelem",
                                     "day",
                                     "month",
                                     "year"]).agg(mean_intensity=("intensidad", "mean")).reset_index()
    
    # Merge with the traffic points to get the district for each point
    traffic_df = traffic_df.merge(traffic_points_df[["idelem", "district"]], on="idelem")
    
    # Group by again, to get nly one value per district per day
    traffic_df = traffic_df.groupby(["district", "day", "month", "year"]).mean()["mean_intensity"].reset_index()
    
    # Get the date and day of the week for plotting purpose
    traffic_df["date"] = pd.to_datetime(traffic_df[["day", "month", "year"]])
    traffic_df["day_of_week"] = traffic_df["date"].dt.day_name()
    
    return traffic_df

In [14]:
def load_all_trafic_data(traffic_points_df):
    """ Function to load all trafic data from the data folder,
        after being processed
        
        Arguments:
            traffic_points_df -> traffic_points dataset (where they are located)
    """
    
    DATA_PATH = "data"
    
    traffic_data = pd.DataFrame([], columns=["district", "date", "day_of_week",
                                             "day", "month", "year", "mean_intensity"])
    
    for filepath in tqdm(os.listdir(DATA_PATH), desc="Processing files", unit="file"):
        traffic_df = process_traffic_data(os.path.join(DATA_PATH, filepath), traffic_points_df)
        
        traffic_data = pd.concat([traffic_data, traffic_df])
    
    return traffic_data.sort_values(by=["district", "date"]).reset_index(drop="True")

In [15]:
df_path = "shared_data/traffic_intensity.csv"

if os.path.isfile(df_path):
    total_traffic_df = pd.read_csv(df_path)
    total_traffic_df["date"] = pd.to_datetime(total_traffic_df["date"])
else:
    total_traffic_df = load_all_trafic_data(traffic_points)
    total_traffic_df.to_csv(df_path, index=False)

total_traffic_df

district       date day_of_week  day  month  year  mean_intensity
0      Arganzuela 2016-01-01      Friday    1      1  2016      397.162405
1      Arganzuela 2016-01-02    Saturday    2      1  2016      433.307174
2      Arganzuela 2016-01-03      Sunday    3      1  2016      401.376015
3      Arganzuela 2016-01-04      Monday    4      1  2016      531.390601
4      Arganzuela 2016-01-05     Tuesday    5      1  2016      524.791899
...           ...        ...         ...  ...    ...   ...             ...
45951  Villaverde 2021-12-27      Monday   27     12  2021      172.038785
45952  Villaverde 2021-12-28     Tuesday   28     12  2021      171.133858
45953  Villaverde 2021-12-29   Wednesday   29     12  2021      175.467792
45954  Villaverde 2021-12-30    Thursday   30     12  2021      187.486617
45955  Villaverde 2021-12-31      Friday   31     12  2021      150.388995

[45956 rows x 7 columns]

In [16]:
p = figure(title="Traffic intensity through time by district", x_axis_label="Date",
           y_axis_label="Traffic intensity", width=800)

fig_lines = []

for name, color in zip(district_name, district_colors):
    source = ColumnDataSource(total_traffic_df[total_traffic_df["district"] == name])
    l = p.line(x="date", y="mean_intensity", source=source,
               color=get_color_from_palette(color), legend_label=name, visible=True,
               line_width=3, alpha=0.8)
    fig_lines.append(l)
    
p.renderers.extend(fig_lines)

    
p.add_layout(p.legend[0], "right")
p.legend.click_policy = "hide"

p.xaxis.formatter=DatetimeTickFormatter(
        days=['%a %d/%m/%Y'],
        months=['%b %Y'],
        years = ['%Y']
    )

# Hover tooltip
TOOLTIPS = [
    ("District", "@district"),
    ("Intensity", "@mean_intensity"),
    ("Day", "@day_of_week @day/@month/@year")
]
p.add_tools(HoverTool(tooltips=TOOLTIPS, mode="vline"))

# Button
button = Button(
    label="Switch all lines visibility", button_type="success", width=100
)
callback = CustomJS(args=dict(lines=fig_lines),
    code="""
    for(var i=0; i<lines.length; i++){
        lines[i].visible = !lines[i].visible;
    }
    """
)
button.js_on_click(callback)

layout = column(p, button)

show(layout)

## Display exploratory analysis focusing on Madrid Central

Now we are going to focus on a more in depth analysis over the *Centro* district.

In [17]:
df_centro = total_traffic_df[total_traffic_df["district"] == "Centro"].reset_index(drop=True)

df_centro

district       date day_of_week  day  month  year  mean_intensity
0      Centro 2016-01-01      Friday    1      1  2016      309.436629
1      Centro 2016-01-02    Saturday    2      1  2016      361.187308
2      Centro 2016-01-03      Sunday    3      1  2016      373.553736
3      Centro 2016-01-04      Monday    4      1  2016      421.640004
4      Centro 2016-01-05     Tuesday    5      1  2016      388.572838
...       ...        ...         ...  ...    ...   ...             ...
2185   Centro 2021-12-27      Monday   27     12  2021      324.816718
2186   Centro 2021-12-28     Tuesday   28     12  2021      330.683128
2187   Centro 2021-12-29   Wednesday   29     12  2021      337.683853
2188   Centro 2021-12-30    Thursday   30     12  2021      343.588872
2189   Centro 2021-12-31      Friday   31     12  2021      275.928293

[2190 rows x 7 columns]

### Year Analysis

First we are going to start focusing on the year evolution, to see whether or not we detect a change in the traffic intensity. Take into account that the Covid-19 lockdown started in Spain the **15th of May of 2020**, and ended the **21st of June of 2020** and that explains a huge decrease in the overall traffic in Madrid.

In [37]:
df_centro_year = df_centro.groupby("year").agg(mean_intensity_year = ("mean_intensity", "mean")).reset_index()

df_year = total_traffic_df.groupby("year").agg(mean_intensity_year = ("mean_intensity", "mean")).reset_index()

display(df_centro_year)
df_year

year  mean_intensity_year
0  2016           424.935031
1  2017           423.296288
2  2018           395.115073
3  2019           387.492076
4  2020           259.084625
5  2021           329.381084

year  mean_intensity_year
0  2016           402.843768
1  2017           395.590693
2  2018           400.240504
3  2019           397.607394
4  2020           294.609887
5  2021           353.196792

In [45]:
p = figure(title="Average traffic intensity per day through the years in Madrid Central and in the city of Madrid", x_axis_label="Year",
           y_axis_label="Traffic intensity average by day", width=800)

source = ColumnDataSource(df_centro_year)
p.vbar(x="year", top="mean_intensity_year", source=source, width=0.5, legend_label="Madrid Central", color=get_color_from_palette(district_colors[0]))

source = ColumnDataSource(df_year)
p.line(x="year", y="mean_intensity_year", source=source, line_width=3, legend_label="Madrid", color=get_color_from_palette(district_colors[1]))

# Hover tooltip
TOOLTIPS = [
    ("Average Intensity per day", "@mean_intensity_year"),
    ("Year", "@year")
    ]
p.add_tools(HoverTool(tooltips=TOOLTIPS, mode="vline"))

p.add_layout(p.legend[0], "right")


show(p)

### Month Analysis

Once we have done a brief analysis over the years, we want to investigate if we are able to detect any pattern in a year using monthly information.

In [70]:
months_name = ["January", "February", "March", "April", "May", "June", "July", "August", "September", "October", "November", "December"]

df_centro_month = df_centro.groupby("month").agg(mean_intensity_month = ("mean_intensity","mean")).reset_index()
df_month = total_traffic_df.groupby("month").agg(mean_intensity_month = ("mean_intensity", "mean")).reset_index()

df_centro_month["month_name"] = df_centro_month.apply(lambda x: months_name[int(x["month"]-1)], axis=1)
df_month["month_name"] = df_month.apply(lambda x: months_name[int(x["month"]-1)], axis=1)


display(df_centro_month)                                                                         
df_month

month  mean_intensity_month month_name
0       1            365.421187    January
1       2            403.588347   February
2       3            373.147824      March
3       4            349.684967      April
4       5            356.627717        May
5       6            382.243448       June
6       7            357.756301       July
7       8            292.520112     August
8       9            387.573064  September
9      10            394.557724    October
10     11            396.332826   November
11     12            381.934985   December

month  mean_intensity_month month_name
0       1            371.945592    January
1       2            405.000396   February
2       3            371.864036      March
3       4            350.500744      April
4       5            366.318699        May
5       6            399.295330       June
6       7            360.723716       July
7       8            279.829494     August
8       9            393.166423  September
9      10            401.314342    October
10     11            402.263363   November
11     12            389.034557   December

In [75]:
p = figure(title="Average traffic intensity per day in a month in Madrid Central and in the city of Madrid", x_axis_label="Month",
           y_axis_label="Traffic intensity average by day", width=1000, x_range=months_name)

source = ColumnDataSource(df_centro_month)
p.vbar(x="month_name", top="mean_intensity_month", source=source, width=0.5, legend_label="Madrid Central", color=get_color_from_palette(district_colors[0]))

source = ColumnDataSource(df_month)
p.line(x="month_name", y="mean_intensity_month", source=source, line_width=3, legend_label="Madrid", color=get_color_from_palette(district_colors[1]))

# Hover tooltip
TOOLTIPS = [
    ("Average Intensity per day", "@mean_intensity_month"),
    ("Month", "@month_name")
    ]
p.add_tools(HoverTool(tooltips=TOOLTIPS, mode="vline"))

p.add_layout(p.legend[0], "right")


show(p)

### Weekly Analysis

Same as with months, we will try now to analyze the weekly traffic change.

In [74]:
week_days = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

df_centro_week = df_centro.groupby("day_of_week").agg(mean_intensity_week = ("mean_intensity", "mean")).reset_index()
df_week = total_traffic_df.groupby("day_of_week").agg(mean_intensity_week = ("mean_intensity", "mean")).reset_index()

df_centro_week["day_of_week"] = df_centro_week["day_of_week"].astype("category")
df_centro_week["day_of_week"] = df_centro_week["day_of_week"].cat.set_categories(week_days)

df_centro_week = df_centro_week.sort_values("day_of_week")


df_week["day_of_week"] = df_week["day_of_week"].astype("category")
df_week["day_of_week"] = df_week["day_of_week"].cat.set_categories(week_days)

df_week = df_week.sort_values("day_of_week")

display(df_centro_week)
df_week

day_of_week  mean_intensity_week
1      Monday           369.592401
5     Tuesday           378.818999
6   Wednesday           387.858992
4    Thursday           396.829133
0      Friday           404.383775
2    Saturday           337.220493
3      Sunday           313.483932

day_of_week  mean_intensity_week
1      Monday           392.625821
5     Tuesday           403.153440
6   Wednesday           409.954094
4    Thursday           415.523900
0      Friday           415.323725
2    Saturday           305.992895
3      Sunday           274.380800

In [80]:
p = figure(title="Average traffic intensity per day in a week in Madrid Central and in the city of Madrid", x_axis_label="Weekday",
           y_axis_label="Traffic intensity average by day", width=1000, x_range=week_days)

source = ColumnDataSource(df_centro_week)
p.vbar(x="day_of_week", top="mean_intensity_week", source=source, width=0.5, legend_label="Madrid Central", color=get_color_from_palette(district_colors[0]))

source = ColumnDataSource(df_week)
p.line(x="day_of_week", y="mean_intensity_week", source=source, line_width=3, legend_label="Madrid", color=get_color_from_palette(district_colors[1]))

# Hover tooltip
TOOLTIPS = [
    ("Average Intensity per day", "@mean_intensity_week"),
    ("Day of the Week", "@day_of_week")
    ]
p.add_tools(HoverTool(tooltips=TOOLTIPS, mode="vline"))

p.add_layout(p.legend[0], "right")


show(p)